In [28]:
import os
import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import DataLoader, Dataset, Subset
from torchvision import transforms
import random
from PIL import Image, ImageDraw, ImageFont, ImageOps, ImageFilter
import cv2
import numpy as np
from torch.optim.lr_scheduler import ReduceLROnPlateau
from sklearn.model_selection import train_test_split
import torch.nn as nn
import torch.nn.functional as F
from tqdm import tqdm

In [43]:
DATASET_DIR = "dataset"
SAVE_PATH = "best_model_10.pth"
BATCH_SIZE = 128
EPOCHS = 30
LEARNING_RATE = 0.01
DEVICE = torch.device("cuda" if torch.cuda.is_available() else "cpu")

CLASSES = "ABEKMHOPCTYX0123456789"
NUM_CLASSES = len(CLASSES)
CLASS_TO_IDX = {char: idx for idx, char in enumerate(CLASSES)}
IDX_TO_CLASS = {idx: char for char, idx in CLASS_TO_IDX.items()}

In [ ]:
FONT_PATH = "RoadNumbers2.0.ttf"
CONFIG_FILE = "dataset_config.txt"
DATASET_DIR = "dataset"  # Папка для итогового датасета
GOSZNAK_DIR = "gosznak"  # Папка с изображениями для аугментаций
REAL_GOSZNAK_DIR = "real_gosznak"  # Папка с реальными изображениями без аугментаций

SYMBOLS = "ABEKMHOPCTYX0123456789"
SMALL_FONT_SIZES = [26, 32]
IMG_SIZE = (28, 28)
FONT_SIZES = [26, 32, 38, 46, 54, 58]
MAX_ROTATION = 10
AUGMENTATIONS = 240

os.makedirs(DATASET_DIR, exist_ok=True)

try:
    font = ImageFont.truetype(FONT_PATH, FONT_SIZES[0])
except IOError:
    print(f"Шрифт {FONT_PATH} не найден. Убедитесь, что он находится в текущей директории.")

def process_gosznak_images(input_dir, output_dir, apply_augmentations=True):
    """
    Обрабатывает изображения из папки `input_dir` и сохраняет их в папку `output_dir`.

    :param input_dir: Путь к папке с исходными изображениями.
    :param output_dir: Путь к папке для сохранения обработанных изображений.
    :param apply_augmentations: Если True, применяются аугментации.
    """
    config_lines = []
    for filename in os.listdir(input_dir):
        filepath = os.path.join(input_dir, filename)
        if not os.path.isfile(filepath) or not filename.endswith((".png", ".jpg", ".jpeg")):
            continue

        img = Image.open(filepath).convert("L")  # Конвертируем в оттенки серого
        img = img.resize(IMG_SIZE, resample=Image.Resampling.LANCZOS)  
        symbol = os.path.splitext(filename)[0][0]  # Предполагаем, что имя файла начинается с символа
        symbol_dir = os.path.join(output_dir, symbol)
        os.makedirs(symbol_dir, exist_ok=True)

        if apply_augmentations:
            for i in range(AUGMENTATIONS):
                aug_img = img.copy()

                # Случайное смещение
                if random.random() < 0.7:
                    aug_img = shift_image(aug_img, max_shift=4)

                # Случайный поворот
                rotation = random.uniform(-MAX_ROTATION, MAX_ROTATION)
                aug_img = aug_img.rotate(rotation, expand=False, fillcolor=255)

                # Случайное расширение
                if random.random() < 0.5:
                    kernel_size = (random.randint(1, 2), random.randint(1, 2))
                    aug_img = expand_characters(aug_img, kernel_size=kernel_size, iterations=1)

                # Случайные разрывы
                if random.random() < 0.15:
                    aug_img = add_random_gaps(aug_img, num_gaps=random.randint(1, 5), gap_size=random.randint(2, 4))

                # Блюр
                #blur_min_limits = {"box": 5, "gaussian": 5, "motion": 6}
                #blur_max_limits = {"box": 10, "gaussian": 10, "motion": 12}
                if random.random() < 0.85:
                    aug_img = apply_blur(aug_img)# blur_min_limits=blur_min_limits, blur_max_limits=blur_max_limits)

                # Добавление шума
                if random.random() < 0.1:
                    aug_img = add_noise(aug_img, intensity=random.randint(10, 20))

                file_path = os.path.join(symbol_dir, f"{symbol}_aug_{i}.png")
                aug_img.save(file_path)
                config_lines.append(f"{file_path},{symbol}\n")
        else:
            # Сохраняем изображение без аугментаций
            file_path = os.path.join(symbol_dir, filename)
            img.save(file_path)
            config_lines.append(f"{file_path},{symbol}\n")
    return config_lines

def expand_characters(img, kernel_size=(2, 2), iterations=1):
    kernel = cv2.getStructuringElement(cv2.MORPH_RECT, kernel_size)
    img_array = np.array(img)
    expanded = cv2.dilate(img_array, kernel, iterations=iterations)
    return Image.fromarray(expanded)

def add_random_gaps(img, num_gaps=5, gap_size=5):
    draw = ImageDraw.Draw(img)
    for _ in range(num_gaps):
        x1 = random.randint(0, IMG_SIZE[0] - gap_size)
        y1 = random.randint(0, IMG_SIZE[1] - gap_size)
        x2 = x1 + gap_size
        y2 = y1 + gap_size
        draw.rectangle([x1, y1, x2, y2], fill=255) 
    return img

def apply_blur(img, blur_min_limits=None, blur_max_limits=None):
    """
    Применяет случайное размытие (BoxBlur, GaussianBlur, MotionBlur) к изображению.

    :param img: PIL Image объект.
    :param blur_min_limits: Словарь с минимальными значениями размытия.
                            Пример: {"box": 1, "gaussian": 1, "motion": 4}.
    :param blur_max_limits: Словарь с максимальными значениями размытия.
                            Пример: {"box": 4, "gaussian": 3, "motion": 8}.
    :return: Изображение с примененным размытием.
    """
    if blur_min_limits is None:
        blur_min_limits = {"box": 1, "gaussian": 1, "motion": 4}

    if blur_max_limits is None:
        blur_max_limits = {"box": 4, "gaussian": 3, "motion": 8}

    blur_type = random.choice(["box", "gaussian", "motion"])

    if blur_type == "box":
        min_radius = blur_min_limits["box"]
        max_radius = blur_max_limits["box"]
        radius = random.randint(min_radius, max_radius)
        img = img.filter(ImageFilter.BoxBlur(radius))

    elif blur_type == "gaussian":
        min_radius = blur_min_limits["gaussian"]
        max_radius = blur_max_limits["gaussian"]
        radius = random.uniform(min_radius, max_radius)
        img = img.filter(ImageFilter.GaussianBlur(radius))

    elif blur_type == "motion":
        min_kernel = blur_min_limits["motion"]
        max_kernel = blur_max_limits["motion"]
        kernel_size = random.randint(min_kernel, max_kernel)
        kernel_motion_blur = np.zeros((kernel_size, kernel_size))
        kernel_motion_blur[int((kernel_size - 1) / 2), :] = 1
        kernel_motion_blur /= kernel_size
        img_array = cv2.filter2D(np.array(img), -1, kernel_motion_blur)
        img = Image.fromarray(img_array)

    return img


def add_noise(img, intensity=30):
    img_array = np.array(img)
    noise = np.random.normal(0, intensity, img_array.shape).astype(np.int32)
    noisy_img = np.clip(img_array + noise, 0, 255).astype(np.uint8)
    return Image.fromarray(noisy_img)

def shift_image(img, max_shift=4):
    """
    Сдвигает изображение на случайное количество пикселей по осям X и Y.

    :param img: PIL Image объект.
    :param max_shift: Максимальное смещение в пикселях по каждой оси.
    :return: Сдвинутое изображение.
    """
    x_shift = random.randint(-max_shift, max_shift)
    y_shift = random.randint(-max_shift, max_shift)
    return img.transform(
        img.size,
        Image.AFFINE,
        (1, 0, x_shift, 0, 1, y_shift),
        fillcolor=255
    )

def create_augmentations(symbol, font_sizes, max_rotation, augmentations, config_lines):
    for i in range(augmentations):
        for font_size in font_sizes:
            current_font = ImageFont.truetype(FONT_PATH, font_size)

            # Создаём пустое изображение с белым фоном
            img = Image.new("L", IMG_SIZE, 255)
            draw = ImageDraw.Draw(img)

            # Получаем размеры текста с использованием Font.getbbox
            text_bbox = draw.textbbox((0, 0), symbol, font=current_font)
            text_width, text_height = text_bbox[2] - text_bbox[0], text_bbox[3] - text_bbox[1]

            # Рассчитываем координаты для центрирования текста
            x = (IMG_SIZE[0] - text_width) // 2 - text_bbox[0]
            y = (IMG_SIZE[1] - text_height) // 2 - text_bbox[1]

            # Рисуем текст
            draw.text((x, y), symbol, font=current_font, fill=0)

            # Для первого прогона символа с данным размером шрифта сохраняем без аугментаций
            if i == 0:
                symbol_dir = os.path.join(DATASET_DIR, symbol)
                os.makedirs(symbol_dir, exist_ok=True)
                file_path = os.path.join(symbol_dir, f"{symbol}_{font_size}_{i}.png")
                img.save(file_path)

                config_lines.append(f"{file_path},{symbol}\n")
                continue

            # Случайное смещение символа
            if random.random() < 0.7: 
                img = shift_image(img, max_shift=4)

            # Случайный поворот изображения
            rotation = random.uniform(-max_rotation, max_rotation)
            img = img.rotate(rotation, expand=False, fillcolor=255)

            # Случайное расширение символов
            if random.random() < 0.5:
                kernel_size = (random.randint(1, 2), random.randint(1, 2))
                iterations = 1
                img = expand_characters(img, kernel_size=kernel_size, iterations=iterations)

            # Случайное добавление разрывов
            if random.random() < 0.15:
                num_gaps = random.randint(1, 5)
                gap_size = random.randint(2, 4)
                img = add_random_gaps(img, num_gaps=num_gaps, gap_size=gap_size)

            # Инверсия цветов с вероятностью 25%
            if random.random() < 0.15:
                img = ImageOps.invert(img)

            # Определяем лимиты блюра в зависимости от размера шрифта
            if font_size in SMALL_FONT_SIZES:
                blur_limits = {"box": 2, "gaussian": 1, "motion": 6}  # Уменьшенные лимиты
            else:
                blur_limits = {"box": 4, "gaussian": 3, "motion": 8}  # Оригинальные лимиты

            # Случайное добавление блюра
            if random.random() < 0.85:
                img = apply_blur(img, blur_max_limits=blur_limits)

            # Случайное добавление шума
            if random.random() < 0.1:
                noise_intensity = random.randint(10, 20)
                img = add_noise(img, intensity=noise_intensity)

            # Сохраняем изображение
            symbol_dir = os.path.join(DATASET_DIR, symbol)
            os.makedirs(symbol_dir, exist_ok=True)
            file_path = os.path.join(symbol_dir, f"{symbol}_{font_size}_{i}.png")
            img.save(file_path)

            config_lines.append(f"{file_path},{symbol}\n")

def main():
    config_lines = []

    for symbol in SYMBOLS:
        create_augmentations(symbol, FONT_SIZES, MAX_ROTATION, AUGMENTATIONS, config_lines)

    config_path = os.path.join(DATASET_DIR, CONFIG_FILE)
    with open(config_path, "w") as config:
        config.writelines(config_lines)

    print(f"Датасет сохранен в папке '{DATASET_DIR}'.")
    print(f"Конфигурационный файл создан: {CONFIG_FILE}")

def main():
    config_lines = []

    for symbol in SYMBOLS:
        create_augmentations(symbol, FONT_SIZES, MAX_ROTATION, AUGMENTATIONS, config_lines)

    config_lines += process_gosznak_images(GOSZNAK_DIR, DATASET_DIR, apply_augmentations=True)

    config_lines += process_gosznak_images(REAL_GOSZNAK_DIR, DATASET_DIR, apply_augmentations=False)

    config_path = os.path.join(DATASET_DIR, CONFIG_FILE)
    with open(config_path, "w") as config:
        config.writelines(config_lines)

    print(f"Датасет сохранен в папке '{DATASET_DIR}'.")
    print(f"Конфигурационный файл создан: {CONFIG_FILE}")

if __name__ == "__main__":
    main()


Датасет сохранен в папке 'dataset'.
Конфигурационный файл создан: dataset_config.txt


In [ ]:
class LicensePlateDataset(Dataset):
    def __init__(self, dataset_dir, transform=None):
        self.data = []
        self.transform = transform
        with open(os.path.join(dataset_dir, "dataset_config.txt"), "r") as file:
            for line in file:
                path, label = line.strip().split(",")
                self.data.append((path, CLASS_TO_IDX[label]))

    def __len__(self):
        return len(self.data)

    def __getitem__(self, idx):
        img_path, label = self.data[idx]
        image = Image.open(img_path).convert("L")
        if self.transform:
            image = self.transform(image)
        return image, label


transform = transforms.Compose([
    transforms.Resize((28, 28), antialias=True), 
    transforms.ToTensor(),
    transforms.RandomResizedCrop(size=(32, 32), scale=(0.8, 1.0), antialias=True),
    transforms.ColorJitter(brightness=0.4, contrast=0.4, saturation=0.4, hue=0.1),
    transforms.RandomAffine(degrees=5, translate=(0.1, 0.1), scale=(0.9, 1.1), shear=5),
    transforms.RandomApply([transforms.GaussianBlur(kernel_size=3, sigma=(0.1, 2.0))], p=0.5),
    transforms.RandomErasing(p=0.3, scale=(0.02, 0.1), ratio=(0.3, 3.3)),
    transforms.Normalize(mean=[0.5], std=[0.5])
])

full_dataset = LicensePlateDataset(DATASET_DIR, transform=transform)

indices = list(range(len(full_dataset)))
train_indices, test_indices = train_test_split(indices, test_size=0.2, random_state=42)

train_dataset = Subset(full_dataset, train_indices)
test_dataset = Subset(full_dataset, test_indices)

train_loader = DataLoader(train_dataset, batch_size=BATCH_SIZE, shuffle=True)
test_loader = DataLoader(test_dataset, batch_size=BATCH_SIZE, shuffle=False)

print(f"Размер тренировочного набора: {len(train_dataset)}")
print(f"Размер тестового набора: {len(test_dataset)}")


Размер тренировочного набора: 29568
Размер тестового набора: 7392


In [56]:
class ImprovedCNN(nn.Module):
    def __init__(self, num_classes):
        super(ImprovedCNN, self).__init__()
        self.conv_layers = nn.Sequential(
            nn.Conv2d(1, 32, kernel_size=2, padding=1),
            nn.LeakyReLU(negative_slope=0.1),
            nn.BatchNorm2d(32),
            nn.MaxPool2d(kernel_size=2, stride=2),

            nn.Conv2d(32, 64, kernel_size=3, padding=1),
            nn.ELU(),
            nn.BatchNorm2d(64),
            nn.MaxPool2d(kernel_size=2, stride=2),

            nn.Conv2d(64, 128, kernel_size=3, padding=1),
            nn.SiLU(),
            nn.BatchNorm2d(128),
            nn.MaxPool2d(kernel_size=2, stride=2),

            nn.Conv2d(128, 256, kernel_size=4, padding=1),
            nn.LeakyReLU(negative_slope=0.1),
            nn.BatchNorm2d(256),
            nn.MaxPool2d(kernel_size=2, stride=2)
        )
        self.fc_layers = nn.Sequential(
            nn.Linear(256, 256),
            nn.GELU(),
            nn.Dropout(0.5),
            nn.Linear(256, num_classes)
        )

    def forward(self, x):
        x = self.conv_layers(x)
        x = x.view(x.size(0), -1) 
        x = self.fc_layers(x)
        return x

In [57]:
model = ImprovedCNN(len(CLASSES)).to(DEVICE)
criterion = nn.CrossEntropyLoss(label_smoothing=0.1)
optimizer = optim.SGD(model.parameters(), lr=LEARNING_RATE, momentum=0.9, weight_decay=1e-4)
#optimizer = torch.optim.Adam(model.parameters(), lr=0.01)
scheduler = ReduceLROnPlateau(optimizer, mode='min', factor=0.1, patience=5)

In [58]:
def train_one_epoch(model, train_loader, optimizer, criterion, device):
    model.train()
    running_loss = 0.0
    correct = 0
    total = 0

    train_bar = tqdm(train_loader, desc="Training", leave=False)
    for images, labels in train_bar:
        images, labels = images.to(device), labels.to(device)

        optimizer.zero_grad()
        outputs = model(images)
        loss = criterion(outputs, labels)
        loss.backward()
        optimizer.step()

        running_loss += loss.item()
        _, predicted = torch.max(outputs, 1)
        total += labels.size(0)
        correct += (predicted == labels).sum().item()

        train_bar.set_postfix(loss=f"{running_loss / len(train_loader):.4f}", acc=f"{100 * correct / total:.2f}%")

    train_loss = running_loss / len(train_loader)
    train_accuracy = 100 * correct / total
    return train_loss, train_accuracy


def evaluate(model, test_loader, criterion, device):
    model.eval()
    running_loss = 0.0
    correct = 0
    total = 0

    with torch.no_grad():
        test_bar = tqdm(test_loader, desc="Testing", leave=False)
        for images, labels in test_bar:
            images, labels = images.to(device), labels.to(device)

            outputs = model(images)
            loss = criterion(outputs, labels)
            running_loss += loss.item()

            _, predicted = torch.max(outputs, 1)
            total += labels.size(0)
            correct += (predicted == labels).sum().item()

    test_loss = running_loss / len(test_loader)
    test_accuracy = 100 * correct / total
    return test_loss, test_accuracy


best_accuracy = 0.0
for epoch in range(EPOCHS):
    print(f"Epoch [{epoch + 1}/{EPOCHS}]")
    train_loss, train_accuracy = train_one_epoch(model, train_loader, optimizer, criterion, DEVICE)
    print(f"Train Loss: {train_loss:.4f}, Train Accuracy: {train_accuracy:.2f}%")

    test_loss, test_accuracy = evaluate(model, test_loader, criterion, DEVICE)
    print(f"Test Loss: {test_loss:.4f}, Test Accuracy: {test_accuracy:.2f}%")

    if test_accuracy > best_accuracy:
        best_accuracy = test_accuracy
        torch.save(model.state_dict(), SAVE_PATH)
        print(f"Best model saved with test accuracy: {best_accuracy:.2f}%")

    if scheduler is not None:
        scheduler.step(test_loss)

print("Обучение завершено.")


Epoch [1/30]


Train Loss: 1.4878, Train Accuracy: 70.34%


Test Loss: 0.9624, Test Accuracy: 90.64%
Best model saved with test accuracy: 90.64%
Epoch [2/30]


Train Loss: 0.9608, Train Accuracy: 91.21%


Test Loss: 0.8277, Test Accuracy: 95.06%
Best model saved with test accuracy: 95.06%
Epoch [3/30]


...

Test Loss: 0.6736, Test Accuracy: 98.53%
Epoch [29/30]


Train Loss: 0.6981, Train Accuracy: 98.41%


Test Loss: 0.6707, Test Accuracy: 98.62%
Best model saved with test accuracy: 98.62%
Epoch [30/30]


Train Loss: 0.6976, Train Accuracy: 98.36%


Test Loss: 0.6715, Test Accuracy: 98.48%
Обучение завершено.


In [59]:
for epoch in range(EPOCHS):
    print(f"Epoch [{epoch + 1}/{EPOCHS}]")
    train_loss, train_accuracy = train_one_epoch(model, train_loader, optimizer, criterion, DEVICE)
    print(f"Train Loss: {train_loss:.4f}, Train Accuracy: {train_accuracy:.2f}%")

    test_loss, test_accuracy = evaluate(model, test_loader, criterion, DEVICE)
    print(f"Test Loss: {test_loss:.4f}, Test Accuracy: {test_accuracy:.2f}%")

    if test_accuracy > best_accuracy:
        best_accuracy = test_accuracy
        torch.save(model.state_dict(), SAVE_PATH)
        print(f"Best model saved with test accuracy: {best_accuracy:.2f}%")

    if scheduler is not None:
        scheduler.step(test_loss)

print("Обучение завершено.")

Epoch [1/30]


Train Loss: 0.6945, Train Accuracy: 98.48%


Test Loss: 0.6733, Test Accuracy: 98.39%
Epoch [2/30]


Train Loss: 0.6948, Train Accuracy: 98.46%


Test Loss: 0.6739, Test Accuracy: 98.16%
Epoch [3/30]


...

Test Loss: 0.6498, Test Accuracy: 98.97%
Epoch [29/30]


Train Loss: 0.6664, Train Accuracy: 99.20%


Test Loss: 0.6498, Test Accuracy: 98.93%
Epoch [30/30]


Train Loss: 0.6663, Train Accuracy: 99.20%


Test Loss: 0.6512, Test Accuracy: 98.85%
Обучение завершено.


In [35]:
from tqdm import tqdm

best_accuracy = 0.0
for epoch in range(EPOCHS):
    model.train()
    running_loss = 0.0
    correct_train = 0
    total_train = 0

    print(f"Epoch [{epoch+1}/{EPOCHS}]")
    train_bar = tqdm(train_loader, desc="Training", leave=False)

    for images, labels in train_bar:
        images, labels = images.to(DEVICE), labels.to(DEVICE)
        optimizer.zero_grad()
        outputs = model(images)
        loss = criterion(outputs, labels)
        loss.backward()
        optimizer.step()

        running_loss += loss.item()
        _, predicted = torch.max(outputs, 1)
        total_train += labels.size(0)
        correct_train += (predicted == labels).sum().item()

        train_bar.set_postfix(loss=f"{running_loss/len(train_loader):.4f}", acc=f"{100 * correct_train / total_train:.2f}%")

    train_accuracy = 100 * correct_train / total_train
    print(f"Train Loss: {running_loss/len(train_loader):.4f}, Train Accuracy: {train_accuracy:.2f}%")

    model.eval()
    correct_test = 0
    total_test = 0
    test_loss = 0.0

    with torch.no_grad():
        test_bar = tqdm(test_loader, desc="Testing", leave=False)
        for images, labels in test_bar:
            images, labels = images.to(DEVICE), labels.to(DEVICE)

            outputs = model(images)
            loss = criterion(outputs, labels)
            test_loss += loss.item()

            _, predicted = torch.max(outputs, 1)
            total_test += labels.size(0)
            correct_test += (predicted == labels).sum().item()

    test_accuracy = 100 * correct_test / total_test
    print(f"Test Loss: {test_loss/len(test_loader):.4f}, Test Accuracy: {test_accuracy:.2f}%")

    if test_accuracy > best_accuracy:
        best_accuracy = test_accuracy
        torch.save(model.state_dict(), SAVE_PATH)
        print(f"Best model saved with test accuracy: {best_accuracy:.2f}%")

print("Обучение завершено.")


Epoch [1/30]


KeyboardInterrupt: 